In [1]:
import pandas as pd
import numpy as np
import math
import operator

In [2]:
alunosUFCG = pd.read_csv('../alunosUFCGAnon.csv', thousands = ',')
alunosUFCG.head()

Matricula  Cod_Curso  Cod_Disciplina  Cod_Evasao                 Nome_Curso  \
0     B7350   14102100         1411191           0  CIÊNCIA DA COMPUTAÇÃO - D   
1     B7350   14102100         1411196           0  CIÊNCIA DA COMPUTAÇÃO - D   
2     B7350   14102100         1411255           0  CIÊNCIA DA COMPUTAÇÃO - D   
3     B7350   14102100         1411173           0  CIÊNCIA DA COMPUTAÇÃO - D   
4     B7350   14102100         1109035           0  CIÊNCIA DA COMPUTAÇÃO - D   

   Periodo                         Nome_Disciplina  Creditos  \
0   2004.2   INTERCONEXÃO DE REDES DE COMPUTADORES         2   
1   2005.1               INTELIGENCIA ARTIFICIAL I         4   
2   2005.1      TECC(LAB DE SISTEMAS OPERACIONAIS)         2   
3   2003.2                       LÓGICA MATEMÁTICA         4   
4   2002.1  ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA         4   

                           Departamento  Media_Disciplina  Situacao  Centro  \
0  UNID. ACAD. DE SISTEMAS E COMPUTAÇÃO               8.5  Aprovado      14   
1  UNID. ACAD. DE SISTEMAS E COMPUTAÇÃO               9.3  Aprovado      14   
2  UNID. ACAD. DE SISTEMAS E COMPUTAÇÃO              10.0  Aprovado      14   
3  UNID. ACAD. DE SISTEMAS E COMPUTAÇÃO               8.7  Aprovado      14   
4             UNID. ACAD. DE MATEMÁTICA               9.3  Aprovado      14   

   Campus  Creditos_Curso         Tipo  Periodo_Ingresso  Periodo_Relativo  
0       1           208.0  Obrigatória            2002.1                 6  
1       1           208.0  Obrigatória            2002.1                 7  
2       1           208.0     Optativa            2002.1                 7  
3       1           208.0  Obrigatória            2002.1                 4  
4       1           208.0  Obrigatória            2002.1                 1

In [3]:
prerequisitos = pd.read_csv('pre_requisitos.tsv', sep='\t')
prerequisitos.head()

codigo_curso  curriculo  codigo_disciplina  codigo_prerequisito
0      13301100       1995            1303002              1303001
1      13301100       1995            1301004              1301001
2      13301100       1995            1109084              1109083
3      13301100       1995            1301063              1301041
4      13301100       1995            1301026              1301005

In [4]:
cadeiras_obrigatorias_df = alunosUFCG[alunosUFCG.Tipo == "Obrigatória"]
cadeiras_obrigatorias_filtradas = cadeiras_obrigatorias_df[['Matricula', 'Cod_Disciplina', 'Nome_Disciplina', 'Periodo', 'Creditos', 'Media_Disciplina', 'Situacao', 'Periodo_Ingresso', 'Periodo_Relativo', 'Nome_Curso']]

In [5]:
COMPUTACAOdf = cadeiras_obrigatorias_filtradas[cadeiras_obrigatorias_df.Nome_Curso =="CIÊNCIA DA COMPUTAÇÃO - D"]
COMPUTACAOtdf = pd.pivot_table(COMPUTACAOdf, values = 'Media_Disciplina', index = ['Nome_Disciplina'], columns = 'Matricula')
print(COMPUTACAOdf)
print(">--------------------------------<")



       Matricula  Cod_Disciplina                           Nome_Disciplina  \
0          B7350         1411191     INTERCONEXÃO DE REDES DE COMPUTADORES   
1          B7350         1411196                 INTELIGENCIA ARTIFICIAL I   
3          B7350         1411173                         LÓGICA MATEMÁTICA   
4          B7350         1109035    ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA   
5          B7350         1411190                     REDES DE COMPUTADORES   
7          B7350         1305220                   INFORMÁTICA E SOCIEDADE   
8          B7350         1411169        PARADIGMAS DE LING. DE PROGRAMAÇÃO   
9          B7350         1411192                     SISTEMAS OPERACIONAIS   
11         B7350         1411181             LABORATÓRIO DE PROGRAMAÇÃO II   
13         B7350         1109103          CALCULO DIFERENCIAL E INTEGRAL I   
14         B7350         1411184  LAB.DE INTERCON.DE REDES DE COMPUTADORES   
15         B7350         1411171                      TEORIA DA 

In [6]:
n_vizinhos = 100
pontos_min_viz = 0.7
n_teste_alunos = 4
n_disci_prox_per = 6
print(COMPUTACAOdf.index)

Int64Index([     0,      1,      3,      4,      5,      7,      8,      9,
                11,     13,
            ...
            442913, 442914, 442915, 442916, 443056, 443057, 443058, 443059,
            443060, 443061],
           dtype='int64', length=33780)


In [8]:
is_number = np.vectorize(lambda x: np.issubdtype(x, np.number))

def get_sim(data_frame):
    data_frame.set_index(data_frame.Matricula) 
    inversa_df = data_frame.transpose()
    resultado = inversa_df[is_number(data_frame)].corr(method='pearson')
    return resultado

def get_neigh(matricula_aluno, df_corr):
    df_corr.at[matricula_aluno, matricula_aluno] = 0
    vizinhos = df_corr[[matricula_aluno,]]

    k_viz_prox = vizinhos.sort_values(by=[matricula_aluno], ascending=False)[1:n_vizinhos+1]
    return k_viz_prox

# como o numero de vizinhos calculado como otimo foi 3(mt pequeno), é necessário prevenir que muitas pessoas
#fiquem sem predição, logo é preciso aumentar a quantidade de vizinhos para aumentar a chance dele ter pago a cadeira em questao
# mas evitar que a precisão da predição diminua por considerar também vizinhos menos semelhantes
def get_nota(data_frame, k_viz_prox, disc_pred):
    notas_vizinhos = data_frame.loc[list(k_vizinhos.index),]
    notas_vizinhos = notas_vizinhos.loc[notas_vizinhos[disc_pred].notnull()]
        
    #se a quantidade de linhas for ==0, ou seja, não tem vizinhos, não há como calcular a nota
    if len(list(notas_vizinhos.index)) == 0:
        return 'NaN'
    
    notas_vizinhos['Similaridade'] = -0.00

    for index, alunos in notas_vizinhos.iterrows():

        notas_vizinhos.at[index,'Similaridade'] = k_viz_prox.at[index,k_viz_prox.columns[0]]

    notas_validas = notas_vizinhos.loc[notas_vizinhos['Similaridade'] > pontos_min_viz]

    
    if(len(notas_validas.index) == 0):
        print('invalida')
        return 'NaN'
    notas_validas = notas_validas.sort_values(by=['Similaridade'], ascending=False)[1:4]
 
    nota_predita = round(sum(notas_validas[disc_pred]*notas_validas['Similaridade'])/ sum(notas_validas['Similaridade']),1)
    return nota_predita

def prox_cadeiras(historico, sem_prerequisito):
    possibilidades = prerequisitos.loc[prerequisitos['codigo_prerequisito'].isin(historico)]
    possibilidades = possibilidades[['codigo_disciplina']]

    for cadeira in possibilidades.codigo_disciplina:
        if not cadeira_paga(cadeira,historico) and cadeira not in sem_prerequisito:
            prerequisitos_cadeira = prerequisitos.loc[prerequisitos['codigo_disciplina'] == cadeira]

            pre=prerequisitos_cadeira['codigo_prerequisito'].isin(historico)
            prerequisitos_pagos = True
            for  c in pre:
                if c == False:
                    prerequisitos_pagos = False
                    break
            if prerequisitos_pagos:
                sem_prerequisito.append(cadeira)
    return sem_prerequisito

def cadeira_paga(cadeira, historico):
    cadeira_isin_historico = False
    for cadeira_paga in historico:
        if cadeira_paga == cadeira:
            cadeira_isin_historico = True
            break
    return cadeira_isin_historico
        
def nomeCadeira_para_cod(conj_cadeiras, cod_nome_df):
    cod_conj_cadeiras = []
    for cadeira in conj_cadeiras:
        aux = cod_nome_df.loc[cod_nome_df['Nome_Disciplina'] == cadeira]
        aux = aux[['Cod_Disciplina']]
        if not aux.empty:
            cod_conj_cadeiras.append(aux.iloc[0]['Cod_Disciplina'])
    return cod_conj_cadeiras

def cod_para_nomeCadeira(conj_cadeiras, cod_nome_df):
    cod_conj_cadeiras = []
    for cadeira in conj_cadeiras:
        aux = cod_nome_df.loc[cod_nome_df['Cod_Disciplina'] == cadeira]
        aux = aux[['Nome_Disciplina']]
    
        if not aux.empty:
            cod_conj_cadeiras.append(aux.iloc[0]['Nome_Disciplina'])
    return cod_conj_cadeiras

# for index, aluno in alunos_predicao.iterrows():
#     cadeiras_pagas = list(aluno.T.dropna().index)
#     prox_possiveis_cadeiras = cod_para_nomeCadeira(prox_cadeiras(cadeiras_pagas, sem_prerequisito),nomeCode_cadeiras)
#     k_vizinhos = get_neigh('B'+str(index), correlacao_alunos)

#     for cadeira in prox_possiveis_cadeiras:
#         print(get_nota(COMPUTACAOtdf.T[[cadeira]],k_vizinhos, cadeira))


In [9]:
cadeiras_cod = COMPUTACAOdf.iloc[:,[1,2]]
cadeiras_code = cadeiras_cod.Cod_Disciplina.unique()
cadeiras_nome = cadeiras_cod.Nome_Disciplina.unique()
nomeCode_cadeiras = pd.DataFrame({"Cod_Disciplina":cadeiras_code, "Nome_Disciplina":cadeiras_nome})
nomeCode_cadeiras.head()

Cod_Disciplina                         Nome_Disciplina
0         1411191   INTERCONEXÃO DE REDES DE COMPUTADORES
1         1411196               INTELIGENCIA ARTIFICIAL I
2         1411173                       LÓGICA MATEMÁTICA
3         1109035  ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA
4         1411190                   REDES DE COMPUTADORES

In [11]:
correlacao_alunos = COMPUTACAOtdf.corr()
alunos_predicao = COMPUTACAOdf
alunos_predicao['Matricula'] = COMPUTACAOdf['Matricula'].map(lambda x: x.lstrip('B'))
alunos_predicao = pd.pivot_table(alunos_predicao, values = 'Media_Disciplina', index = ['Matricula'], columns = 'Nome_Disciplina')



/home/livia.cavalcanti/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [13]:
for i in range(1276):
    alunos_predicao = alunos_predicao.sample(n=4)
    for index, aluno in alunos_predicao.iterrows():
        cadeiras_pagas = list(aluno.T.dropna().index)
        prox_possiveis_cadeiras = cod_para_nomeCadeira(prox_cadeiras(cadeiras_pagas, sem_prerequisito),nomeCode_cadeiras)
        k_vizinhos = get_neigh('B'+str(index), correlacao_alunos)
        dict_notas = {}

        for cadeira in prox_possiveis_cadeiras:
            dict_notas[cadeira] = math.trunc(get_nota(COMPUTACAOtdf.T[[cadeira]],k_vizinhos, cadeira)*10)
        
#         list_notas = sorted()
        print("Notas do historico do aluno:")
        print(aluno.T.dropna())
        print("-----------")
        print("Notas preditas: ")
        for cadeira in dict_notas: 
            print(cadeira, ": ", dict_notas[cadeira]/10)
        print("================")


Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          5.20
CALCULO DIFERENCIAL E INTEGRAL II         3.25
ESTRUTURA DE DADOS E ALGORITMOS           6.50
FUNDAMENTOS DE FÍSICA CLÁSSICA            9.10
FUNDAMENTOS DE FÍSICA MODERNA             7.10
GERÊNCIA DA INFORMAÇÃO                    7.50
INFORMÁTICA E SOCIEDADE                   8.30
INTRODUÇÃO A COMPUTAÇÃO                   7.30
LAB.DE ESTRUTURA DE DADOS E ALGORITMOS    7.10
LABORATÓRIO DE PROGRAMAÇÃO I              6.20
LABORATÓRIO DE PROGRAMAÇÃO II             7.80
LEITURA E PRODUCAO DE TEXTOS              7.00
MATEMÁTICA DISCRETA                       5.30
PROBABILIDADE E ESTATISTICA               3.40
PROGRAMAÇÃO I                             6.20
PROGRAMAÇÃO II                            7.90
TEORIA DA COMPUTAÇÃO                      4.20
TEORIA DOS GRAFOS                         7.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    5.50
Name: 4753, dtype: float64
-----------
Notas preditas: 
DIREIT

METODOLOGIA CIENTÍFICA :  9.4
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.9
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          1.30
INTRODUÇÃO A COMPUTAÇÃO                   7.00
LABORATÓRIO DE PROGRAMAÇÃO I              4.00
MATEMÁTICA DISCRETA                       3.40
PROGRAMAÇÃO I                             4.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    0.45
Name: 9671, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  8.5
GERÊNCIA DA INFORMAÇÃO :  7.4
INFORMÁTICA E SOCIEDADE :  2.7
MATEMÁTICA DISCRETA :  4.9
METODOLOGIA CIENTÍFICA :  9.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.8
Notas do historico do aluno:
Nome_Disciplina
ANÁLISE E TÉCNICA DE ALGORITMOS             5.7
AVAL.DE DESEMPENHO DE SISTEMAS DISCRETOS    7.9
BANCO DE DADOS I                            7.0
BANCO DE DADOS II                           7.8
CALCULO DIFERENCIAL E INTEGRAL I            6.3
COMPILADORES                                8.7
DIREITO E CIDADANIA            

Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          5.20
CALCULO DIFERENCIAL E INTEGRAL II         3.25
ESTRUTURA DE DADOS E ALGORITMOS           6.50
FUNDAMENTOS DE FÍSICA CLÁSSICA            9.10
FUNDAMENTOS DE FÍSICA MODERNA             7.10
GERÊNCIA DA INFORMAÇÃO                    7.50
INFORMÁTICA E SOCIEDADE                   8.30
INTRODUÇÃO A COMPUTAÇÃO                   7.30
LAB.DE ESTRUTURA DE DADOS E ALGORITMOS    7.10
LABORATÓRIO DE PROGRAMAÇÃO I              6.20
LABORATÓRIO DE PROGRAMAÇÃO II             7.80
LEITURA E PRODUCAO DE TEXTOS              7.00
MATEMÁTICA DISCRETA                       5.30
PROBABILIDADE E ESTATISTICA               3.40
PROGRAMAÇÃO I                             6.20
PROGRAMAÇÃO II                            7.90
TEORIA DA COMPUTAÇÃO                      4.20
TEORIA DOS GRAFOS                         7.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    5.50
Name: 4753, dtype: float64
-----------
Notas preditas: 
DIREIT

Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          5.20
CALCULO DIFERENCIAL E INTEGRAL II         3.25
ESTRUTURA DE DADOS E ALGORITMOS           6.50
FUNDAMENTOS DE FÍSICA CLÁSSICA            9.10
FUNDAMENTOS DE FÍSICA MODERNA             7.10
GERÊNCIA DA INFORMAÇÃO                    7.50
INFORMÁTICA E SOCIEDADE                   8.30
INTRODUÇÃO A COMPUTAÇÃO                   7.30
LAB.DE ESTRUTURA DE DADOS E ALGORITMOS    7.10
LABORATÓRIO DE PROGRAMAÇÃO I              6.20
LABORATÓRIO DE PROGRAMAÇÃO II             7.80
LEITURA E PRODUCAO DE TEXTOS              7.00
MATEMÁTICA DISCRETA                       5.30
PROBABILIDADE E ESTATISTICA               3.40
PROGRAMAÇÃO I                             6.20
PROGRAMAÇÃO II                            7.90
TEORIA DA COMPUTAÇÃO                      4.20
TEORIA DOS GRAFOS                         7.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    5.50
Name: 4753, dtype: float64
-----------
Notas preditas: 
DIREIT

SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.9
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          3.9
INTRODUÇÃO A COMPUTAÇÃO                   0.0
LABORATÓRIO DE PROGRAMAÇÃO I              2.6
LEITURA E PRODUCAO DE TEXTOS              7.0
PROGRAMAÇÃO I                             2.6
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    3.5
Name: 22895, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  9.0
GERÊNCIA DA INFORMAÇÃO :  6.9
INFORMÁTICA E SOCIEDADE :  5.8
MATEMÁTICA DISCRETA :  6.3
METODOLOGIA CIENTÍFICA :  8.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.5
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          5.20
CALCULO DIFERENCIAL E INTEGRAL II         3.25
ESTRUTURA DE DADOS E ALGORITMOS           6.50
FUNDAMENTOS DE FÍSICA CLÁSSICA            9.10
FUNDAMENTOS DE FÍSICA MODERNA             7.10
GERÊNCIA DA INFORMAÇÃO                    7.50
INFORMÁTICA E SOCIEDADE                   8.30
INTRODUÇÃO A COMPUTAÇÃO  

...

-----------
Notas preditas: 
DIREITO E CIDADANIA :  9.0
GERÊNCIA DA INFORMAÇÃO :  5.7
INFORMÁTICA E SOCIEDADE :  8.0
MATEMÁTICA DISCRETA :  2.1
METODOLOGIA CIENTÍFICA :  5.7
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  5.6
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          3.9
INTRODUÇÃO A COMPUTAÇÃO                   0.0
LABORATÓRIO DE PROGRAMAÇÃO I              2.6
LEITURA E PRODUCAO DE TEXTOS              7.0
PROGRAMAÇÃO I                             2.6
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    3.5
Name: 22895, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  9.0
GERÊNCIA DA INFORMAÇÃO :  6.9
INFORMÁTICA E SOCIEDADE :  5.8
MATEMÁTICA DISCRETA :  6.3
METODOLOGIA CIENTÍFICA :  8.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.5
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          1.30
INTRODUÇÃO A COMPUTAÇÃO                   7.00
LABORATÓRIO DE PROGRAMAÇÃO I              4.00
MATEMÁTICA DISCRETA                    

INFORMÁTICA E SOCIEDADE :  5.8
MATEMÁTICA DISCRETA :  6.3
METODOLOGIA CIENTÍFICA :  8.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.5
Notas do historico do aluno:
Nome_Disciplina
ANÁLISE E TÉCNICA DE ALGORITMOS             5.7
AVAL.DE DESEMPENHO DE SISTEMAS DISCRETOS    7.9
BANCO DE DADOS I                            7.0
BANCO DE DADOS II                           7.8
CALCULO DIFERENCIAL E INTEGRAL I            6.3
COMPILADORES                                8.7
DIREITO E CIDADANIA                         8.0
ENGENHARIA DE SOFTWARE I                    7.4
ESTRUTURA DE DADOS E ALGORITMOS             7.2
FUNDAMENTOS DE FÍSICA CLÁSSICA              5.4
FUNDAMENTOS DE FÍSICA MODERNA               7.4
GERÊNCIA DA INFORMAÇÃO                      8.3
INFORMÁTICA E SOCIEDADE                     9.0
INTELIGENCIA ARTIFICIAL I                   6.7
INTERCONEXÃO DE REDES DE COMPUTADORES       7.0
INTRODUÇÃO A COMPUTAÇÃO                     8.3
LAB.DE ESTRUTURA DE DADOS E ALGORITMOS      7.8
LAB.DE INTER

SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.9
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          1.30
INTRODUÇÃO A COMPUTAÇÃO                   7.00
LABORATÓRIO DE PROGRAMAÇÃO I              4.00
MATEMÁTICA DISCRETA                       3.40
PROGRAMAÇÃO I                             4.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    0.45
Name: 9671, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  8.5
GERÊNCIA DA INFORMAÇÃO :  7.4
INFORMÁTICA E SOCIEDADE :  2.7
MATEMÁTICA DISCRETA :  4.9
METODOLOGIA CIENTÍFICA :  9.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.8
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          5.20
CALCULO DIFERENCIAL E INTEGRAL II         3.25
ESTRUTURA DE DADOS E ALGORITMOS           6.50
FUNDAMENTOS DE FÍSICA CLÁSSICA            9.10
FUNDAMENTOS DE FÍSICA MODERNA             7.10
GERÊNCIA DA INFORMAÇÃO                    7.50
INFORMÁTICA E SOCIEDADE                   8.30
INTRODUÇÃO A COMPUTA

Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          3.9
INTRODUÇÃO A COMPUTAÇÃO                   0.0
LABORATÓRIO DE PROGRAMAÇÃO I              2.6
LEITURA E PRODUCAO DE TEXTOS              7.0
PROGRAMAÇÃO I                             2.6
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    3.5
Name: 22895, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  9.0
GERÊNCIA DA INFORMAÇÃO :  6.9
INFORMÁTICA E SOCIEDADE :  5.8
MATEMÁTICA DISCRETA :  6.3
METODOLOGIA CIENTÍFICA :  8.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.5
Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          1.30
INTRODUÇÃO A COMPUTAÇÃO                   7.00
LABORATÓRIO DE PROGRAMAÇÃO I              4.00
MATEMÁTICA DISCRETA                       3.40
PROGRAMAÇÃO I                             4.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    0.45
Name: 9671, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  8.5
GERÊNCIA DA INFORMAÇÃO :  7.

Notas do historico do aluno:
Nome_Disciplina
CALCULO DIFERENCIAL E INTEGRAL I          1.30
INTRODUÇÃO A COMPUTAÇÃO                   7.00
LABORATÓRIO DE PROGRAMAÇÃO I              4.00
MATEMÁTICA DISCRETA                       3.40
PROGRAMAÇÃO I                             4.00
ÁLGEBRA VETORIAL E GEOMETRIA ANALÍTICA    0.45
Name: 9671, dtype: float64
-----------
Notas preditas: 
DIREITO E CIDADANIA :  8.5
GERÊNCIA DA INFORMAÇÃO :  7.4
INFORMÁTICA E SOCIEDADE :  2.7
MATEMÁTICA DISCRETA :  4.9
METODOLOGIA CIENTÍFICA :  9.1
SEMINÁRIOS (EDUCAÇÃO AMBIENTAL) :  8.8
Notas do historico do aluno:
Nome_Disciplina
ANÁLISE E TÉCNICA DE ALGORITMOS             5.7
AVAL.DE DESEMPENHO DE SISTEMAS DISCRETOS    7.9
BANCO DE DADOS I                            7.0
BANCO DE DADOS II                           7.8
CALCULO DIFERENCIAL E INTEGRAL I            6.3
COMPILADORES                                8.7
DIREITO E CIDADANIA                         8.0
ENGENHARIA DE SOFTWARE I                    7.4
ESTR